<a href="https://colab.research.google.com/github/SciEcon/UTXO/blob/main/UTXO_Visualizations.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Import Packages

In [1]:
import numpy as np # linear algebra
import pandas as pd
import decimal
import plotly.graph_objects as go
from plotly.offline import iplot
import plotly.express as px
import plotly.offline as py     
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Define the Class Object

In [17]:
result = pd.read_csv(STXOaddress)
result.head()

-9   -7   -5   -3   -1    1  ...    9      date  newborn  dead  WAL   11
0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  2009/1/3     50.0   0.0  0.0  0.0
1  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  2009/1/4      0.0   0.0  0.0  0.0
2  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  2009/1/5      0.0   0.0  0.0  0.0
3  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  2009/1/6      0.0   0.0  0.0  0.0
4  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  2009/1/7      0.0   0.0  0.0  0.0

[5 rows x 15 columns]

In [18]:
Dist_Alive = pd.read_csv(UTXOaddress)
Dist_Alive.head()

-9    -7   -5   -3   -1    1    3    5    7    9      date   11
0  50.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2009/1/3  0.0
1   0.0  50.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2009/1/4  0.0
2   0.0  50.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2009/1/5  0.0
3   0.0  50.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2009/1/6  0.0
4   0.0  50.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2009/1/7  0.0

In [21]:
data3 = 'https://raw.githubusercontent.com/coinmetrics-io/data/master/csv/'+currency_brief+'.csv'
price = pd.read_csv(data3)
price.head()

time  AdrActCnt  ...  VtyDayRet180d  VtyDayRet30d
0  2009-01-03        0.0  ...            NaN           NaN
1  2009-01-04        0.0  ...            NaN           NaN
2  2009-01-05        0.0  ...            NaN           NaN
3  2009-01-06        0.0  ...            NaN           NaN
4  2009-01-07        0.0  ...            NaN           NaN

[5 rows x 144 columns]

In [22]:
categories=['-9', '-7', '-5', '-3', '-1', '1', '3', '5', '7', '9', '11']
Result = result
Result[categories] = Result[categories].cumsum(axis=0)
Result['net_new'] = Result['newborn'] - Result['dead']
Result['UTXO_Cum'] = Result['net_new'].cumsum()
Result['dead_cum'] = Result['dead'].cumsum()
Result['lifelength_cum'] = (Result['dead'].mul(Result['WALE'])).cumsum()
Result['WALE_cum'] = Result['lifelength_cum']/Result['dead_cum']

KeyError: ignored

In [29]:
class UTXO:
  def __init__(self, STXOaddress, UTXOaddress,currency,currency_brief):
    self.currency_brief=currency_brief
    self.currency = currency
    self.STXO = STXOaddress
    self.UTXO = UTXOaddress
    data1 = STXOaddress
    data2 = UTXOaddress
    data3 = 'https://raw.githubusercontent.com/coinmetrics-io/data/master/csv/'+self.currency_brief+'.csv'
    result = pd.read_csv(data1)
    Dist_Alive = pd.read_csv(data2)
    price = pd.read_csv(data3)
    categories=['-9', '-7', '-5', '-3', '-1', '1', '3', '5', '7', '9', '11']
    price["Date"] = pd.to_datetime(price["time"], format='%Y-%m-%d')
    price = price[["Date", "PriceUSD"]]
    Result = result
    Result[categories] = Result[categories].cumsum(axis=0)
    Result['net_new'] = Result['newborn'] - Result['dead']
    Result['UTXO_Cum'] = Result['net_new'].cumsum()
    Result['dead_cum'] = Result['dead'].cumsum()
    Result['lifelength_cum'] = (Result['dead'].mul(Result['WALE'])).cumsum()
    Result['WALE_cum'] = Result['lifelength_cum']/Result['dead_cum']
    result = pd.read_csv(data1)
    self.result = result
    self.Result = Result
    self.Dist_Alive = Dist_Alive
    self.price = price
  def Dist(self):
    Result = self.Result
    trace0 = go.Scatter(x = Result["date"], y = Result.UTXO_Cum, hoverinfo='x+y', mode='lines', stackgroup='one', groupnorm='percent', name = 'Accumulated UTXO in '+self.currency)
    trace1 = go.Scatter(x = Result["date"], y = Result.dead_cum, hoverinfo='x+y', mode='lines', stackgroup='one', name = 'Accumulated STXO in '+self.currency)
    layout = go.Layout(title="Distribution of UTXO and Accumulated STXO in "+currency, xaxis = dict(title="date"), yaxis = dict(title ="Percentage") ) 
    data = [trace0, trace1]
    fig1 = go.Figure(layout = layout, data = data) 
    fig1.update_yaxes(type="log")
    fig1.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig1)
    return fig1
  def Dist_UTXO(self):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    trace0 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["-9"], hoverinfo='x+y', mode='lines', stackgroup='one', groupnorm='percent', name = '< 1d', line=dict(color="#f0f921"))
    trace1 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["-7"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1d ~ 1m', line=dict(color="#fdca26"))
    trace2 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["-5"]+Dist_Alive["-3"]+Dist_Alive["-1"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1m ~ 1y', line=dict(color="#fb9f3a"))
    trace3 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["1"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1y ~ 2y', line=dict(color="#d8576b"))
    trace4 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["3"]+Dist_Alive["5"]+Dist_Alive["7"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '2y ~ 5y', line=dict(color="#9c179e"))
    trace5 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["9"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '5y ~ 10y', line=dict(color="#46039f"))
    trace6 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["11"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '> 10y', line=dict(color="#0d0887"))
    fig2 = make_subplots(specs=[[{"secondary_y": True}]])
    fig2.add_trace(trace6)
    fig2.add_trace(trace5)
    fig2.add_trace(trace4)
    fig2.add_trace(trace3)
    fig2.add_trace(trace2)
    fig2.add_trace(trace1)
    fig2.add_trace(trace0)
    fig2.add_trace(go.Scatter(x=price['Date'], y=price['PriceUSD'], mode='lines', name='Price', line=dict(color="black")), secondary_y=True)
    fig2.update_layout(title="Age Distribution of UTXOs and Prices for "+self.currency, xaxis = dict(title="date"), yaxis = dict(title ="Percentage") ) 
    fig2.update_yaxes(type="log", title_text ="Price (USD)", secondary_y=True)
    fig2.update_yaxes(tickvals=[0.1, 1, 10, 100, 1000, 10000], secondary_y=True)
    fig2.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=0.95
    ))
    fig2.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig2)
    return fig2

  def Dist_UTXO_num(self):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    trace0 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["-9"], name = '< 1d', line=dict(color="#f0f921"))
    trace1 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["-7"], name = '1d ~ 1m', line=dict(color="#fb9f3a"))
    trace2 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["-5"]+Dist_Alive["-3"]+Dist_Alive["-1"], name = '1m ~ 1y', line=dict(color="#d8576b"))
    trace3 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["1"], name = '1y ~ 2y', line=dict(color="#9c179e"))
    trace4 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["3"]+Dist_Alive["5"]+Dist_Alive["7"], name = '2y ~ 5y', line=dict(color="#7201a8"))
    trace5 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["9"], name = '5y~10y', line=dict(color="#46039f"))
    trace6 = go.Scatter(x = Dist_Alive["date"], y = Dist_Alive["11"], name = '>10y', line=dict(color="#0d0887"))
    layout = go.Layout(title= "UTXOs by Age in "+self.currency, xaxis = dict(title="date"), yaxis = dict(title ="UTXOs in "+self.currency) ) 
    data = [trace0, trace1, trace2, trace3, trace4, trace5, trace6]
    fig3 = go.Figure(layout = layout, data = data) 
    fig3.update_yaxes(type="log")
    fig3.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ))
    fig3.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig3)
    return fig3
  def Dist_STXO(self):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    trace0 = go.Scatter(x = Result["date"], y = Result["-9"], hoverinfo='x+y', mode='lines', stackgroup='one', groupnorm='percent', name = '< 1d', line=dict(color="#f0f921"))
    trace1 = go.Scatter(x = Result["date"], y = Result["-7"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1d ~ 1m', line=dict(color="#fb9f3a"))
    trace2 = go.Scatter(x = Result["date"], y = Result["-5"]+Result["-3"]+Result["-1"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1m ~ 1y', line=dict(color="#d8576b"))
    trace3 = go.Scatter(x = Result["date"], y = Result["1"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1y ~ 2y', line=dict(color="#9c179e"))
    trace4 = go.Scatter(x = Result["date"], y = Result["3"]+Result["5"]+Result["7"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '2y ~ 5y', line=dict(color="#7201a8"))
    trace5 = go.Scatter(x = Result["date"], y = Result["9"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '5y ~ 10y', line=dict(color="#46039f"))
    trace6 = go.Scatter(x = Result["date"], y = Result["11"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '> 10y', line=dict(color="#0d0887"))
    layout = go.Layout(title="Lifespan Distribution of Accumulated STXOs for "+self.currency, xaxis = dict(title="Date"), yaxis = dict(title ="Percentage") ) 
    data = [trace6, trace5, trace4, trace3, trace2, trace1, trace0]
    fig4 = go.Figure(layout = layout, data = data) 
    fig4.update_yaxes(type="log")
    fig4.update_yaxes(tickvals=[0.1, 0.2, 0.5, 1, 2, 5, 10, 20, 50, 100])
    fig4.update_yaxes(range=[-1.2, 2])
    fig4.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ))
    fig4.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig4)
    return fig4

  def Dist_STXO_num(self):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    trace0 = go.Scatter(x = Result["date"], y = Result["-9"], name = '< 1d')
    trace1 = go.Scatter(x = Result["date"], y = Result["-7"], name = '1d ~ 1m')
    trace2 = go.Scatter(x = Result["date"], y = Result["-5"]+Result["-3"]+Result["-1"], name = '1m ~ 1y')
    trace3 = go.Scatter(x = Result["date"], y = Result["1"], name = '1y ~ 2y')
    trace4 = go.Scatter(x = Result["date"], y = Result["3"]+Result["5"]+Result["7"], name = '2y ~ 5y')
    trace5 = go.Scatter(x = Result["date"], y = Result["9"], name = '5y ~ 10y')
    trace6 = go.Scatter(x = Result["date"], y = Result["11"], name = '> 10y')

    layout = go.Layout(title="Accumulated STXOs by Lifespan in "+self.currency, xaxis = dict(title="date"), yaxis = dict(title ="STXO") ) 
    data = [trace0, trace1, trace2, trace3, trace4, trace5, trace6]
    fig5 = go.Figure(layout = layout, data = data) 
    fig5.update_yaxes(type="log")
    fig5.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ))
    fig5.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig5)
    return fig5
  def Dist_daiy_STXO(self):
    result = self.result
    Dist_Alive = self.Dist_Alive
    price = self.price
    trace0 = go.Scatter(x = result["date"], y = result["-9"], hoverinfo='x+y', mode='lines', stackgroup='one', groupnorm='percent', name = '< 1d', line=dict(color="#f0f921"))
    trace1 = go.Scatter(x = result["date"], y = result["-7"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1d ~ 1m', line=dict(color="#fb9f3a"))
    trace2 = go.Scatter(x = result["date"], y = result["-5"]+result["-3"]+result["-1"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1m ~ 1y', line=dict(color="#d8576b"))
    trace3 = go.Scatter(x = result["date"], y = result["1"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '1y ~ 2y', line=dict(color="#9c179e"))
    trace4 = go.Scatter(x = result["date"], y = result["3"]+result["5"]+result["7"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '2y ~ 5y', line=dict(color="#7201a8"))
    trace5 = go.Scatter(x = result["date"], y = result["9"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '5y ~ 10y', line=dict(color="#46039f"))
    trace6 = go.Scatter(x = result["date"], y = result["11"], hoverinfo='x+y', mode='lines', stackgroup='one', name = '> 10y', line=dict(color="#0d0887"))
    layout = go.Layout(title="Lifespan Distribution of the Daily STXOs in "+self.currency, xaxis = dict(title="date"), yaxis = dict(title ="Percentage") ) 
    data = [trace6, trace5, trace4, trace3, trace2, trace1, trace0]
    fig6 = go.Figure(layout = layout, data = data) 
    fig6.update_yaxes(type="log")
    fig6.update_yaxes(tickvals=[0.1, 0.2, 0.5, 1, 2, 5, 10, 20, 50, 100])
    fig6.update_yaxes(range=[-1.5, 2])
    fig6.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ))
    fig6.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig6)
    return fig6
  def WAL(self):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    fig7 = px.line(Result, x = 'date', y = 'WALE_cum', title = 'Weighted Average Lifespan of Accumulated STXO for '+self.currency)
    fig7.update_layout(xaxis_title='Date', yaxis_title='Days')
    fig7.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig7)
    return fig7
  def Supply(self):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    import plotly.offline as py     
    import plotly.graph_objects as go
    fig8 = go.Figure()
    fig8.add_trace(go.Scatter(x=Result.date, y=Result.net_new,
                  mode='markers', name='block reward', marker=dict(size=4)))
    fig8.add_trace(go.Scatter(x=Result.date, y=Result.UTXO_Cum, yaxis="y2",
                  mode='lines', name='circulating supply', line=dict(color="red")))
    fig8.add_trace(go.Scatter(x=Result.date, y=Result.dead_cum, yaxis="y3",
                  mode='lines', name='total spent', line=dict(color="black")))
    fig8.update_yaxes(range=[0, 16000])
    fig8.update_layout(legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    ))
    fig8.update_layout(title='Block rewards, circulating supply (UTXO), and total spent (accumulated STXO) of  ' + self.currency,
              xaxis_title='Date',
              xaxis=dict(domain=[0,0.9]),
              yaxis1=dict(title="", tickfont=dict(color="blue")),
              yaxis2=dict(
                title="",
                titlefont=dict(color="red"),
                tickfont=dict(color="red"),
              anchor="x",
              overlaying="y",
              side="right"),
              yaxis3=dict(
                title="",
                titlefont=dict(color="black"),
                tickfont=dict(color="black"),
              anchor="free",
              overlaying="y",
              side="right",
              position=0.95)
    )
    fig8.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig8)
    return fig8
  def Velocity(self,days):
    Result = self.Result
    Dist_Alive = self.Dist_Alive
    price = self.price
    for i in range(days,len(Result)):
      Result['STXO_diff'] = Result['dead_cum'].diff(days)
    Result['velocity'] = Result['STXO_diff']/Result['UTXO_Cum']
    fig9 = make_subplots(specs=[[{"secondary_y": True}]])
    fig9.add_trace(go.Scatter(x=Result['date'], y=Result['velocity'], mode='lines', name='Token Velocity'), secondary_y=False )
    fig9.add_trace(go.Scatter(x=price['Date'], y=price['PriceUSD'], mode='lines', name='Price'), secondary_y=True )
    fig9.update_layout(xaxis_title='Date', yaxis_title='Velocity', title = 'Token Velocity and Price for '+self.currency)
    fig9.update_yaxes(type="log", title_text ="Price (USD)", secondary_y=True)
    fig9.update_yaxes(tickvals=[0.1, 1, 10, 100, 1000, 10000], secondary_y=True)
    fig9.update_layout(legend=dict(
          orientation="h",
          yanchor="bottom",
          y=1.02,
          xanchor="right",
          x=0.95
      ))
    fig9.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(step="all"),
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=3, label="3m", step="month", stepmode="backward"),
            dict(count=3, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
          
        ])))
    py.iplot(fig9)
    return fig9

# Generate the Sample Figures for Bitcoin

## Call the Bitcoin Instance

In [27]:
currency = "Bitcoin" 
currency_brief ="btc"
STXOaddress = "https://raw.githubusercontent.com/SciEcon/UTXO/main/BitcoinResultSTXO2021-02-10.csv"
UTXOaddress = "https://raw.githubusercontent.com/SciEcon/UTXO/main/BitcoinResultUTXO2021-02-10.csv"

In [30]:
Bitcoin = UTXO(STXOaddress,UTXOaddress,currency,currency_brief)

## Figure 1: Dist of Accumulated UTXO and STXO

In [26]:
Dist = Bitcoin.Dist()

## Figure 2: Dist of Accumulated/Daily UTXO and STXO respectively

### Figure 2.1 UTXO

In [31]:
Dist_UTXO = Bitcoin.Dist_UTXO()

### Figure 2.2: UTXO (NUM)

In [32]:
Dist_UTXO_numb = Bitcoin.Dist_UTXO_num()

### Figure 2.3 Accumulated STXO

In [33]:
Dist_STXO = Bitcoin.Dist_STXO()

### Figure 2.4 Accumulated STXO

In [34]:
Dist_STXO_num = Bitcoin.Dist_STXO_num()

### Figure 2.5 Daily STXO

In [35]:
Dist_daily_STXO = Bitcoin.Dist_daiy_STXO()

### Figure 2.6 WAL

In [36]:
WAL = Bitcoin.WAL()

## Figure 3: Other Variables of Economic Value

### Figure 3.1: Supply

In [37]:
Supply = Bitcoin.Supply()

In [38]:
days=60
Velocity1 =Bitcoin.Velocity(days)

In [39]:
days=30
Velocity2 =Bitcoin.Velocity(days)